In [1]:
import os
import sys

In [2]:
import itertools

In [3]:
import numpy as np
import pandas as pd
from scipy.io import loadmat
from scipy import signal

import matplotlib.pyplot as plt
import plotly.express as px

In [4]:
import functools

In [5]:
import numpy as np
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import balanced_accuracy_score
from sklearn.preprocessing import StandardScaler
import shap


In [6]:
from biosppy.signals import ecg
from biosppy.signals.eda import basic_scr
from  biosppy.signals.eda import eda

In [7]:
import hrvanalysis as hrvana

from hrvanalysis import remove_outliers
from hrvanalysis import remove_ectopic_beats
from hrvanalysis import interpolate_nan_values

from hrvanalysis import get_time_domain_features
from hrvanalysis import get_geometrical_features
from hrvanalysis import get_frequency_domain_features
from hrvanalysis import get_csi_cvi_features
from hrvanalysis import get_poincare_plot_features
from hrvanalysis import get_sampen

In [8]:
from statsmodels.multivariate.manova import MANOVA

In [9]:
import xgboost

In [10]:
from numpy.lib.stride_tricks import as_strided as stride

In [11]:
# !pip install git+https://github.com/skjerns/mat7.3

In [12]:
import mat73


In [13]:
info_df = pd.read_csv('info_df_20210421.csv')

In [14]:
s_df = pd.read_csv('s_df_20210421.csv')

In [15]:
s_df = pd.read_csv('s_expand_df_20210422.csv')

In [16]:
s_df['emo_expr_h'] = s_df['emo_expr'] > 5
s_df['tech_diff_h'] = s_df['tech_diff'] > 5

In [17]:
ecols = ['excerpt','trial','user','tech_diff','emo_expr','feel_calm','feel_nervous','feel_at_ease','feel_uncomfortable']
s_df.groupby(['excerpt_category','tempo'])[['tech_diff','emo_expr','feel_calm','feel_nervous','feel_at_ease','feel_uncomfortable','nirvana']].mean()


tech_diff  emo_expr  feel_calm  feel_nervous  \
excerpt_category tempo                                                   
repertoire       average   9.000000  8.357143   4.214286      5.785714   
                 fast      7.285714  8.857143   5.428571      4.857143   
                 slow      3.642857  9.357143   7.142857      2.928571   
technical        fast      4.190476  3.345238   7.071429      3.297619   
                 slow      3.238095  3.571429   7.857143      2.488095   

                          feel_at_ease  feel_uncomfortable    nirvana  
excerpt_category tempo                                                 
repertoire       average      4.357143            4.928571  11.445112  
                 fast         5.714286            5.000000  14.613133  
                 slow         7.142857            3.928571  19.123164  
technical        fast         7.261905            4.142857  18.873003  
                 slow         7.892857            3.928571  20.860660

In [18]:
s_df.groupby(['excerpt_category','tempo'])[['tech_diff','emo_expr']].agg(['mean','count'])

tech_diff        emo_expr      
                              mean count      mean count
excerpt_category tempo                                  
repertoire       average  9.000000    14  8.357143    14
                 fast     7.285714     7  8.857143     7
                 slow     3.642857    14  9.357143    14
technical        fast     4.190476    84  3.345238    84
                 slow     3.238095    84  3.571429    84

In [19]:
s_df.groupby(['tech_diff'])[['feel_calm','feel_nervous','feel_at_ease','feel_uncomfortable','nirvana']].mean()


feel_calm  feel_nervous  feel_at_ease  feel_uncomfortable  \
tech_diff                                                              
1.0         9.208333      1.625000      9.166667            4.750000   
2.0         7.914286      2.800000      7.771429            4.114286   
3.0         7.230769      2.794872      7.435897            4.435897   
4.0         7.111111      3.111111      7.333333            3.888889   
5.0         6.777778      4.166667      7.166667            5.166667   
6.0         5.937500      4.187500      6.000000            3.750000   
7.0         6.857143      2.666667      7.047619            2.476190   
8.0         5.923077      4.000000      6.000000            3.538462   
9.0         5.000000      5.250000      4.750000            5.000000   
10.0        3.500000      6.833333      4.000000            5.000000   

             nirvana  
tech_diff             
1.0        24.039046  
2.0        20.565163  
3.0        19.581019  
4.0        19.122479  
5.0        17.817499  
6.0        15.901869  
7.0        18.954530  
8.0        16.033164  
9.0        13.003819  
10.0        9.592423

In [20]:
s_df.groupby(['emo_expr'])[['feel_calm','feel_nervous','feel_at_ease','feel_uncomfortable','nirvana']].mean()


feel_calm  feel_nervous  feel_at_ease  feel_uncomfortable    nirvana
emo_expr                                                                      
1.0        8.258065      2.322581      8.387097            4.580645  21.838910
2.0        7.580645      2.870968      7.548387            3.806452  19.973880
3.0        7.631579      2.552632      7.605263            3.263158  20.323848
4.0        6.941176      3.235294      7.529412            3.941176  19.034044
5.0        7.000000      3.739130      7.217391            5.217391  18.418037
6.0        6.600000      3.350000      7.000000            4.250000  18.123095
7.0        6.714286      4.714286      5.857143            3.714286  16.139564
8.0        5.200000      5.800000      5.200000            6.400000  13.184913
9.0        5.555556      4.055556      5.833333            4.444444  15.471158
10.0       6.615385      3.153846      6.538462            3.307692  17.871914

In [21]:
# data = pd.read_csv('data_20210322.csv')
# data = pd.read_csv('data_w30_s10_20210422.csv')
data = pd.read_csv('data_w30_s5_20210428.csv')
data['timestamp'] = data['timestamp'].apply(pd.Timestamp)

In [22]:
data = data.replace([np.inf, -np.inf], np.nan, inplace=False)

In [23]:
gsr_cols = [c for c in data.columns if c.split('_')[0] == 'gsr']

In [24]:
window_features = [col for col in data.columns if col.split('_')[0].lower() in ['imu','gyr','hrv','gsr']]

In [25]:
bl_df = data[data.trial.str.contains('base')]

In [26]:
def pd_mean_skipna(x):
    return x.mean(skipna=True)


def pd_std_skipna(x):
    return x.std(skipna=True)

In [27]:
# data = pd.merge(data, data.groupby(['user','is_baseline'])['v_gps'].max().reset_index(drop=False).rename(columns={'v_gps':'v_gps_max'}), on=['personId','source'])
data_bl_mean = bl_df[bl_df.trial == 'base1'].groupby(['user'])[window_features].agg([pd_mean_skipna]).reset_index(drop=False).rename(columns={col:col+'_bl_mean' for col in window_features})
data_bl_mean = data_bl_mean.replace([np.inf, -np.inf], np.nan, inplace=False)
data_bl_mean.columns = [col_name[0] for col_name in data_bl_mean.columns.to_flat_index()]
data_bl_std = bl_df[bl_df.trial == 'base1'].groupby(['user'])[window_features].agg([pd_std_skipna]).reset_index(drop=False).rename(columns={col:col+'_bl_std' for col in window_features})
data_bl_std = data_bl_std.replace([np.inf, -np.inf], np.nan, inplace=False)
data_bl_std.columns = [col_name[0] for col_name in data_bl_std.columns.to_flat_index()]

In [28]:
gsr_cols = [c for c in data.columns if 'gsr' in c]
s_df['nirvana_int'] = s_df['nirvana'].fillna(0).astype(int)
print(pd.merge(data, s_df, on=['user','trial']).groupby(['nirvana_int'])[gsr_cols].mean().reset_index().corr())
px.scatter(pd.merge(data, s_df, on=['user','trial']).groupby(['nirvana_int'])[gsr_cols].mean().reset_index(), 'nirvana_int','gsr_SHA_var')

                      nirvana_int  gsr_SHF_n_peaks  gsr_SHF_max_peak_amp  \
nirvana_int              1.000000         0.626007             -0.138903   
gsr_SHF_n_peaks          0.626007         1.000000             -0.113495   
gsr_SHF_max_peak_amp    -0.138903        -0.113495              1.000000   
gsr_SHF_mean            -0.106422        -0.084864              0.995505   
gsr_SHF_var             -0.511433        -0.539865              0.330257   
gsr_SHA_n_peaks          0.138511         0.472971             -0.036970   
gsr_SHA_max_peak_amp    -0.348454        -0.036303              0.287611   
gsr_SHA_mean            -0.265904        -0.002063              0.239664   
gsr_SHA_var             -0.730722        -0.439158              0.291076   
gsr_SHS_n_peaks          0.530826         0.615633              0.003085   
gsr_SHS_max_peak_amp    -0.553104        -0.342406              0.303835   
gsr_SHS_mean            -0.535235        -0.385236              0.278102   
gsr_SHS_var 

In [29]:
nan_cols_bl = data_bl_std.isna().T[np.logical_and.reduce([data_bl_std.isna().T[ci] == True for ci in data_bl_std.isna().T.columns])].index.to_list()

nan_cols_bl_mean = data_bl_mean.isna().T[np.logical_and.reduce([data_bl_mean.isna().T[ci] == True for ci in data_bl_mean.isna().T.columns])].index.to_list()
nan_cols_bl = [c[:c.find('_bl')] for c in nan_cols_bl] 
nan_cols_bl_mean = [c[:c.find('_bl')] for c in nan_cols_bl_mean]
nan_cols_bl = nan_cols_bl + nan_cols_bl_mean + ['hrv_sampen']
nan_cols_bl += [f"GYR_{i}_{j}_ent" for i,j in itertools.product(['A','B'],[0,1,2])] 
nan_cols_bl += [f"GYR_{i}_{j}_jerk_ent" for i,j in itertools.product(['A','B'],[0,1,2])] 

nan_cols_bl = list(np.unique(nan_cols_bl))
nan_cols_bl_mean = [c + '_bl_mean' for c in nan_cols_bl]
nan_cols_bl_std = [c + '_bl_std' for c in nan_cols_bl]
nan_cols_bl

['GYR_A_0_ent',
 'GYR_A_0_jerk_ent',
 'GYR_A_1_ent',
 'GYR_A_1_jerk_ent',
 'GYR_A_2_ent',
 'GYR_A_2_jerk_ent',
 'GYR_B_0_ent',
 'GYR_B_0_jerk_ent',
 'GYR_B_1_ent',
 'GYR_B_1_jerk_ent',
 'GYR_B_2_ent',
 'GYR_B_2_jerk_ent',
 'IMU_A_0_ent',
 'IMU_A_0_jerk_ent',
 'IMU_A_1_ent',
 'IMU_A_1_jerk_ent',
 'IMU_A_2_jerk_ent',
 'IMU_B_0_ent',
 'IMU_B_0_jerk_ent',
 'IMU_B_1_ent',
 'IMU_B_1_jerk_ent',
 'IMU_B_2_jerk_ent',
 'hrv_sampen',
 'hrv_tinn']

In [30]:
bl_gsr_desc = bl_df.fillna(-1)[gsr_cols].describe()
bl_gsr_desc.T[bl_gsr_desc.T['std'] != 0].T

gsr_SHF_n_peaks  gsr_SHF_max_peak_amp  gsr_SHF_mean  gsr_SHF_var  \
count       364.000000            364.000000    364.000000   364.000000   
mean          3.032967              9.479619      9.573861     0.196223   
std           2.114885              4.012385      3.852619     0.137390   
min          -1.000000             -1.000000     -1.000000    -1.000000   
25%           2.000000              7.746607      7.690423     0.095908   
50%           3.000000              8.971796      8.872758     0.180607   
75%           4.000000             11.769805     11.774798     0.254944   
max          14.000000             28.449105     28.353946     0.626911   

       gsr_SHA_n_peaks  gsr_SHA_max_peak_amp  gsr_SHA_mean  gsr_SHA_var  \
count       364.000000            364.000000    364.000000   364.000000   
mean          3.337912              1.597159      1.566953    -0.143661   
std           3.304324              2.149945      2.042166     0.478192   
min          -1.000000             -1.000000     -1.000000    -1.000000   
25%           1.000000              0.407559      0.408067     0.001211   
50%           3.000000              0.890413      0.898961     0.005986   
75%           5.000000              3.434825      3.424227     0.027972   
max          11.000000              8.977848      8.283620     1.832339   

       gsr_SHS_n_peaks  gsr_SHS_max_peak_amp  gsr_SHS_mean  gsr_SHS_var  
count       364.000000            364.000000    364.000000   364.000000  
mean          2.574176              0.669879      0.716359    -0.308007  
std           3.906270              1.473053      1.471712     0.475407  
min          -1.000000             -1.000000     -1.000000    -1.000000  
25%          -1.000000             -1.000000     -1.000000    -1.000000  
50%           1.500000              0.635778      0.669044     0.002257  
75%           4.000000              1.691814      1.664861     0.006350  
max          14.000000              4.479823      4.526547     0.378090

In [31]:
data_gsr_desc = data.fillna(-1)[gsr_cols].describe()
data_gsr_desc.T[data_gsr_desc.T['std'] != 0].T

gsr_SHF_n_peaks  gsr_SHF_max_peak_amp  gsr_SHF_mean  gsr_SHF_var  \
count      2088.000000           2088.000000   2088.000000  2088.000000   
mean          5.542625             12.950709     12.796152     0.291187   
std           3.548703              6.938401      6.694629     0.281254   
min          -1.000000             -1.000000     -1.000000    -1.000000   
25%           3.000000              8.335332      8.314685     0.123587   
50%           5.000000             12.184887     12.058423     0.204641   
75%           7.000000             13.830448     13.665158     0.359155   
max          21.000000             37.285398     36.481422     2.764414   

       gsr_SHA_n_peaks  gsr_SHA_max_peak_amp  gsr_SHA_mean  gsr_SHA_var  \
count      2088.000000           2088.000000   2088.000000  2088.000000   
mean          3.177203              2.596085      2.555711    -0.072220   
std           3.253720              2.520353      2.400798     0.477773   
min          -1.000000             -1.000000     -1.000000    -1.000000   
25%           1.000000              0.412219      0.649247     0.002655   
50%           3.000000              2.049785      2.588079     0.023128   
75%           5.000000              4.657406      4.578602     0.089290   
max          15.000000              9.544646     10.199036     1.832339   

       gsr_SHS_n_peaks  gsr_SHS_max_peak_amp  gsr_SHS_mean  gsr_SHS_var  
count      2088.000000           2088.000000   2088.000000  2088.000000  
mean          4.014368              1.461780      1.471482    -0.123814  
std           4.269972              1.863451      1.766622     0.462260  
min          -1.000000             -1.000000     -1.000000    -1.000000  
25%           1.000000              0.577109      0.628529     0.000795  
50%           3.000000              1.383836      1.397768     0.003161  
75%           7.000000              1.829166      1.834590     0.020853  
max          16.000000              9.634441      8.956675     1.873709

In [32]:
bl_na_desc = bl_df.fillna(-1)[nan_cols_bl].describe()
bl_na_desc.T[bl_na_desc.T['std'] != 0].T

GYR_A_0_ent  GYR_A_1_ent  GYR_A_2_ent  GYR_B_0_ent  GYR_B_1_ent  \
count   364.000000   364.000000   364.000000   364.000000   364.000000   
mean      0.429862     3.329540     2.330057     3.128570     3.378764   
std       3.288807     4.505583     4.343102     4.490264     4.506953   
min      -1.000000    -1.000000    -1.000000    -1.000000    -1.000000   
25%      -1.000000    -1.000000    -1.000000    -1.000000    -1.000000   
50%      -1.000000    -1.000000    -1.000000    -1.000000    -1.000000   
75%      -1.000000     8.005521     7.976236     7.998571     8.005069   
max       7.983761     8.005673     7.986147     8.001149     8.005359   

       GYR_B_2_ent  hrv_sampen  
count   364.000000  364.000000  
mean      1.317338    1.189192  
std       3.932828    0.759284  
min      -1.000000   -1.000000  
25%      -1.000000    0.871406  
50%      -1.000000    1.252763  
75%       7.961415    1.635000  
max       7.983142    3.135494

In [33]:
px.histogram(bl_df.fillna(-1), 'GYR_A_1_ent')

In [34]:
px.histogram(bl_df.fillna(-1), 'hrv_sampen')

### The mean of the SHF GSR sensor data appears to have 2 different distributions

In [35]:
px.histogram(data.fillna(-1), 'gsr_SHF_mean')

In [36]:
px.histogram(bl_df.fillna(-1), 'gsr_SHF_mean')

In [37]:
px.scatter(bl_df.fillna(-1).reset_index(), 'index', 'gsr_SHF_mean', facet_row='user', facet_col='trial', color='gsr_SHF_mean')

In [38]:
data = pd.merge(data, s_df, on=['user','trial'])


In [39]:
data['is_baseline'] = data.trial.str.contains('base')

In [40]:
data_bl_mean.shape

(7, 301)

In [41]:
data_bl_mean.isna().sum().sum()

154

In [42]:
bl_mean_na_cols = data_bl_mean.columns[data_bl_mean.isna().any()].tolist()
bl_std_na_cols = data_bl_std.columns[data_bl_std.isna().any()].tolist()
print(bl_mean_na_cols)
print()
print(bl_std_na_cols)
print()
print(list(set(data_bl_mean.columns[data_bl_mean.isna().any()].tolist()) | set(data_bl_std.columns[data_bl_std.isna().any()].tolist())))

['IMU_A_0_ent_bl_mean', 'IMU_A_1_ent_bl_mean', 'IMU_A_2_ent_bl_mean', 'IMU_B_0_ent_bl_mean', 'IMU_B_1_ent_bl_mean', 'IMU_B_2_ent_bl_mean', 'GYR_A_0_ent_bl_mean', 'GYR_A_1_ent_bl_mean', 'GYR_A_2_ent_bl_mean', 'GYR_B_0_ent_bl_mean', 'GYR_B_1_ent_bl_mean', 'GYR_B_2_ent_bl_mean', 'IMU_A_0_jerk_ent_bl_mean', 'IMU_A_1_jerk_ent_bl_mean', 'IMU_A_2_jerk_ent_bl_mean', 'IMU_B_0_jerk_ent_bl_mean', 'IMU_B_1_jerk_ent_bl_mean', 'IMU_B_2_jerk_ent_bl_mean', 'GYR_A_0_jerk_ent_bl_mean', 'GYR_A_1_jerk_ent_bl_mean', 'GYR_A_2_jerk_ent_bl_mean', 'GYR_B_0_jerk_ent_bl_mean', 'GYR_B_1_jerk_ent_bl_mean', 'GYR_B_2_jerk_ent_bl_mean', 'hrv_tinn_bl_mean', 'gsr_SHA_n_peaks_bl_mean', 'gsr_SHA_max_peak_amp_bl_mean', 'gsr_SHA_mean_bl_mean', 'gsr_SHA_var_bl_mean', 'gsr_SHS_n_peaks_bl_mean', 'gsr_SHS_max_peak_amp_bl_mean', 'gsr_SHS_mean_bl_mean', 'gsr_SHS_var_bl_mean']

['IMU_A_0_ent_bl_std', 'IMU_A_1_ent_bl_std', 'IMU_A_2_ent_bl_std', 'IMU_B_0_ent_bl_std', 'IMU_B_1_ent_bl_std', 'IMU_B_2_ent_bl_std', 'GYR_A_0_ent_bl_std',

In [43]:
# data[window_features] = ((data[window_features] - (pd.merge(data[['user']], data_bl_mean).drop('user',axis=1).values)) / (pd.merge(data[['user']], data_bl_std).drop('user',axis=1).values*1e5))

In [44]:
# Optionally normalize 
# data[window_features] = (data[window_features] / (pd.merge(data[['user']], data_bl_mean).drop('user',axis=1).values))

In [45]:

#data.groupby('user')[data.columns[data[data.trial.str.contains('trial')].isna().any()].tolist()].count()
# for c in data.columns[data[data.trial.str.contains('trial')].isna().any()].tolist():
#     print(c)

In [46]:
data = data.drop(data.columns[data[data.trial.str.contains('trial')].isna().any()].tolist(), axis=1)

In [47]:
data['inv_nervous'] = 10 - data['feel_nervous']
data['feel_good'] = data[['feel_calm','feel_at_ease','inv_nervous']].apply(np.mean, axis=1)

In [48]:
data.groupby(['user','feel_nervous']).mean().reset_index().corr().iloc[40:80,:]

user  feel_nervous  IMU_A_0_mean  IMU_A_0_median  \
IMU_B_2_skew    0.164714     -0.168025      0.226874       -0.048730   
IMU_B_2_kurt   -0.130498     -0.179614     -0.007043        0.087074   
IMU_B_2_iqr     0.047894      0.526076     -0.346532       -0.072031   
IMU_B_2_rmssd   0.184306      0.534839     -0.394182        0.027733   
GYR_A_0_mean    0.108475      0.067733      0.157155        0.162553   
GYR_A_0_median  0.158028      0.108613     -0.061856       -0.155059   
GYR_A_0_var     0.531092      0.137095     -0.117359        0.073456   
GYR_A_0_skew   -0.197241     -0.248184     -0.042346        0.068866   
GYR_A_0_kurt   -0.087675     -0.089265      0.152779        0.285802   
GYR_A_0_iqr     0.423431      0.076473     -0.210538       -0.077799   
GYR_A_0_rmssd   0.358510      0.127516      0.027675        0.072166   
GYR_A_1_mean    0.018197      0.265816     -0.404869        0.071783   
GYR_A_1_median  0.064911      0.115948      0.083425       -0.124199   
GYR_A_1_var     0.160424      0.107363      0.081948        0.083819   
GYR_A_1_skew    0.026456      0.201172     -0.141470        0.176922   
GYR_A_1_kurt   -0.023808     -0.219491      0.231748        0.236321   
GYR_A_1_iqr     0.358554      0.050943     -0.164147       -0.089489   
GYR_A_1_rmssd   0.254130      0.088624      0.026577        0.087130   
GYR_A_2_mean   -0.090596      0.436494      0.304321        0.355221   
GYR_A_2_median  0.137017     -0.088689     -0.090359       -0.200360   
GYR_A_2_var     0.345173     -0.136019     -0.189050       -0.233829   
GYR_A_2_skew   -0.087771     -0.022416      0.103018        0.428352   
GYR_A_2_kurt   -0.017271     -0.025738      0.273122        0.298312   
GYR_A_2_iqr     0.238411     -0.135924     -0.246669       -0.242773   
GYR_A_2_rmssd   0.307759      0.094472     -0.101203       -0.064092   
GYR_B_0_mean   -0.138151      0.019629      0.371063        0.442916   
GYR_B_0_median -0.240240      0.054089      0.041368        0.158351   
GYR_B_0_var     0.552315     -0.045968     -0.158264       -0.390465   
GYR_B_0_skew    0.042730     -0.102465     -0.043921        0.133255   
GYR_B_0_kurt   -0.055826     -0.106485      0.247401        0.335831   
GYR_B_0_iqr     0.433732     -0.046380     -0.246829       -0.393933   
GYR_B_0_rmssd   0.258144      0.056876     -0.097855       -0.124203   
GYR_B_1_mean   -0.067170      0.006315      0.181466        0.020813   
GYR_B_1_median  0.331520     -0.001818     -0.176017       -0.395110   
GYR_B_1_var     0.294385     -0.061620     -0.207878       -0.359816   
GYR_B_1_skew   -0.329271      0.032808      0.063969        0.210256   
GYR_B_1_kurt   -0.038084     -0.261263      0.228861        0.241028   
GYR_B_1_iqr     0.258134     -0.006227     -0.226585       -0.359223   
GYR_B_1_rmssd   0.256042      0.043678     -0.160840       -0.161460   
GYR_B_2_mean   -0.190451      0.026178     -0.069482        0.252030   

                IMU_A_0_var  IMU_A_0_skew  IMU_A_0_kurt  IMU_A_0_iqr  \
IMU_B_2_skew      -0.318669     -0.188211      0.320021    -0.289819   
IMU_B_2_kurt      -0.149531     -0.143776      0.754006    -0.313448   
IMU_B_2_iqr        0.640570      0.170560     -0.573082     0.789002   
IMU_B_2_rmssd      0.599767     -0.015971     -0.302844     0.671086   
GYR_A_0_mean      -0.200343     -0.005543      0.273345    -0.222032   
GYR_A_0_median    -0.037087      0.232464      0.013934    -0.107949   
GYR_A_0_var        0.271524     -0.068653      0.076285     0.291030   
GYR_A_0_skew      -0.131703      0.034859      0.085636    -0.058695   
GYR_A_0_kurt       0.025812     -0.306566      0.396059    -0.095883   
GYR_A_0_iqr        0.223365      0.088184     -0.040434     0.297534   
GYR_A_0_rmssd      0.194463     -0.076976      0.289096     0.196298   
GYR_A_1_mean       0.194617      0.078439     -0.051263     0.230446   
GYR_A_1_median     0.231452      0.205368      0.207284     0.165777   
GYR_A_1_var       -0.014831     -0.027069      0.385600    

In [49]:
data.min()


user                                1
trial                           base1
timestamp         2021-01-01 00:00:15
IMU_A_0_mean                -0.127339
IMU_A_0_median              -0.928148
                         ...         
emo_expr_h                      False
tech_diff_h                     False
nirvana_int                         0
is_baseline                     False
feel_good                    0.666667
Length: 291, dtype: object

In [50]:
data.corr()

user  IMU_A_0_mean  IMU_A_0_median  IMU_A_0_var  \
user            1.000000      0.084192       -0.115948     0.214827   
IMU_A_0_mean    0.084192      1.000000        0.228154    -0.096310   
IMU_A_0_median -0.115948      0.228154        1.000000     0.180834   
IMU_A_0_var     0.214827     -0.096310        0.180834     1.000000   
IMU_A_0_skew    0.049834     -0.010864       -0.416260    -0.106066   
...                  ...           ...             ...          ...   
emo_expr_h     -0.020761     -0.033818       -0.082105     0.114974   
tech_diff_h     0.219162     -0.048808       -0.185999     0.315428   
nirvana_int    -0.160847      0.019182       -0.055151     0.005474   
is_baseline     0.022251      0.023800        0.000932    -0.268936   
feel_good      -0.252403      0.075656       -0.101796    -0.398869   

                IMU_A_0_skew  IMU_A_0_kurt  IMU_A_0_iqr  IMU_A_0_rmssd  \
user                0.049834     -0.077739     0.198606       0.194269   
IMU_A_0_mean       -0.010864     -0.009300    -0.079800      -0.111772   
IMU_A_0_median     -0.416260     -0.016640     0.093273       0.162421   
IMU_A_0_var        -0.106066     -0.204655     0.863859       0.895759   
IMU_A_0_skew        1.000000     -0.314560    -0.000873      -0.133265   
...                      ...           ...          ...            ...   
emo_expr_h          0.041794      0.010043     0.152917       0.188043   
tech_diff_h         0.273327     -0.089275     0.380298       0.331679   
nirvana_int         0.149003     -0.098736     0.173709       0.220295   
is_baseline        -0.041649      0.120711    -0.391092      -0.461037   
feel_good           0.226039      0.001550    -0.280715      -0.324895   

                IMU_A_1_mean  IMU_A_1_median  ...  feel_nervous  emo_expr  \
user               -0.082173       -0.032743  ...      0.179155 -0.047602   
IMU_A_0_mean       -0.019773       -0.028894  ...     -0.096743 -0.049102   
IMU_A_0_median     -0.129781        0.452230  ...      0.195221 -0.037249   
IMU_A_0_var         0.055657       -0.049546  ...      0.382619  0.055769   
IMU_A_0_skew       -0.081162       -0.204989  ...     -0.288197  0.121714   
...                      ...             ...  ...           ...       ...   
emo_expr_h          0.007939       -0.112541  ...      0.171489  0.790455   
tech_diff_h         0.023919       -0.171876  ...      0.269027  0.203034   
nirvana_int        -0.015567       -0.026790  ...     -0.880248 -0.258804   
is_baseline        -0.019899        0.022564  ...           NaN       NaN   
feel_good          -0.061543       -0.016430  ...     -0.892968 -0.259462   

                piece_id  inv_nervous   nirvana  emo_expr_h  tech_diff_h  \
user            0.084560    -0.179155 -0.257481   -0.020761     0.219162   
IMU_A_0_mean    0.040907     0.096743  0.074132   -0.033818    -0.048808   
IMU_A_0_median  0.045553    -0.195221 -0.093049   -0.082105    -0.185999   
IMU_A_0_var     0.050856    -0.382619 -0.397109    0.114974     0.315428   
IMU_A_0_skew    0.053959     0.288197  0.219589    0.041794     0.273327   
...                  ...          ...       ...         ...          ...   
emo_expr_h      0.414778    -0.171489 -0.255806    1.000000     0.236223   
tech_diff_h     0.228151    -0.269027 -0.397920    0.236223     1.000000   
nirvana_int    -0.292794     0.880248  0.998965    0.201429    -0.002957   
is_baseline          NaN          NaN       NaN   -0.407015    -0.264952   
feel_good      -0.289794     0.892968  0.999457   -0.252179    -0.392075   

                nirvana_int  is_baseline  feel_good  
user              -0.160847     0.022251  -0.252403  
IMU_A_0_mean       0.019182     0.023800   0.075656  
IMU_A_0_median    -0.055151     0.000932  -0.101796  
IMU_A_0_var        0.005474    -0.268936  -0.398869  
IMU_A_0_skew       0.149003    -0.041649   0.226039  
...                     ...          ...        ...  
emo_expr_h         0.201429    -0.407015  -0.252179  
tech_dif

In [131]:
data_corr_melt_df = data.corr().reset_index().melt(id_vars=['index'])
filt_a = ((data_corr_melt_df['value'] > 0.5) | (data_corr_melt_df['value'] < -0.5))
filt_b = ((data_corr_melt_df['value'] < 1) & (data_corr_melt_df['value'] > -1))
filt_c = (data_corr_melt_df['index'].str.lower().str.contains('nirvana') | (data_corr_melt_df['index'].str.lower().str.contains('feel_uncomfortable')) | (data_corr_melt_df['index'].str.lower().str.contains('tech_diff')))
filt_d = (~data_corr_melt_df['variable'].str.lower().str.contains('nirvana') & (~data_corr_melt_df['variable'].str.lower().str.contains('feel')) & (~data_corr_melt_df['variable'].str.lower().str.contains('tech_diff')))

with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(data_corr_melt_df[filt_a & filt_b & filt_c & filt_d])

index                  variable     value
278    feel_uncomfortable                      user -0.619369
3215            tech_diff               IMU_A_1_var  0.503366
4391            tech_diff             IMU_A_1_rmssd  0.526836
7331            tech_diff               IMU_B_0_var  0.521677
26147           tech_diff       imu_a_magnitude_var  0.541326
26155             nirvana       imu_a_magnitude_var -0.511690
28499           tech_diff       imu_b_magnitude_var  0.519228
29381           tech_diff       imu_b_magnitude_iqr  0.529000
60259             nirvana  imu_a_jerk_magnitude_var -0.513684
60266        tech_diff_vh  imu_a_jerk_magnitude_var  0.500439
68780  feel_uncomfortable              hrv_mean_nni -0.543396
71132  feel_uncomfortable            hrv_median_nni -0.550105
72308  feel_uncomfortable               hrv_mean_hr  0.508095
72602  feel_uncomfortable                hrv_max_hr  0.545439
79070  feel_uncomfortable                  HR_Hzpsd  0.528718
79952  feel_uncomfortable                hr_bpm_med  0.531000
83191             nirvana               inv_nervous  0.878086
83194         nirvana_int               inv_nervous  0.880248
84664         nirvana_int               is_baseline -0.819260
86428         nirvana_int                   bl_flag -0.819260

In [51]:
data['tech_diff_h'] = (data['tech_diff'] > 5).astype(int)
data['feel_nervous_h'] = (data['feel_nervous'] > 5).astype(int)

In [52]:
corr_df = data.corr().reset_index().rename(columns={'index':'row'}).melt(id_vars=['row'], value_vars=list(set(data.corr().columns) - set(['duration', 'timestamp', 'trial'])))
filt_row = np.logical_or.reduce([corr_df['row'] == c for c in ['tech_diff', 'feel_calm', 'feel_at_ease', 'feel_uncomfortable', 'feel_nervous', 'emo_expr', 'tech_diff_h', 'feel_nervous_h','tech_diff_h','emo_expr_h','nirvana']])
filt_col = np.logical_and.reduce([corr_df['variable'] != c for c in ['user','excerpt','tech_diff', 'feel_calm', 'feel_at_ease', 'feel_uncomfortable', 'feel_nervous', 'emo_expr', 'tech_diff_h', 'feel_nervous_h', 'feel_good', 'inv_nervous','tech_diff_h','emo_expr_h','nirvana','piece_id']])

In [53]:
data['tech_diff_vh'] = data['tech_diff'] > 7

In [54]:
data['emo_expr_vh'] = data['emo_expr'] > 7

In [55]:
px.scatter_3d(data[data.trial.str.contains('trial')], x='imu_a_magnitude_iqr', y='gsr_SHF_mean', z='gsr_SHF_var', color='feel_nervous_h')

In [56]:
px.scatter_3d(data[data.trial.str.contains('trial')], x='imu_a_magnitude_iqr', y='hrv_ratio_sd2_sd1', z='gsr_SHF_var', color='emo_expr_h')

In [57]:
thr = 0.51#0.45
corr_df[filt_row & filt_col][((corr_df.value > thr) & (corr_df.value < 1)) | (corr_df.value < -1*thr)].sort_values('value')

<ipython-input-57-956f518ee8af>:2: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



row                  variable     value
16519        feel_nervous               nirvana_int -0.880248
22318  feel_uncomfortable            hrv_median_nni -0.550105
70168  feel_uncomfortable              hrv_mean_nni -0.543396
45813             nirvana  imu_a_jerk_magnitude_var -0.513684
8693              nirvana       imu_a_magnitude_var -0.511690
80895           tech_diff       imu_b_magnitude_var  0.519228
76835           tech_diff               IMU_B_0_var  0.521677
53345           tech_diff             IMU_A_1_rmssd  0.526836
46098  feel_uncomfortable                  HR_Hzpsd  0.528718
3175            tech_diff       imu_b_magnitude_iqr  0.529000
73358  feel_uncomfortable                hr_bpm_med  0.531000
8685            tech_diff       imu_a_magnitude_var  0.541326
67268  feel_uncomfortable                hrv_max_hr  0.545439
16517        feel_at_ease               nirvana_int  0.946121
16516           feel_calm               nirvana_int  0.957422
16523             nirvana               nirvana_int  0.998965

In [58]:
px.scatter(data[data.trial.str.contains('trial')], x='imu_a_magnitude_iqr', y='imu_b_magnitude_mean', color='feel_nervous', facet_row='user')

In [59]:
px.scatter_3d(data, x='gsr_SHF_mean', y='gsr_SHF_var', z='imu_a_magnitude_var', color='feel_nervous')

In [60]:
px.scatter(data[data.trial.str.contains('trial')], x='gsr_SHF_mean', y='gsr_SHF_var', color='feel_calm', facet_row='user')

In [61]:
px.scatter(data, x='gsr_SHF_max_peak_amp', y='gsr_SHF_var', color='tech_diff')

In [62]:
px.scatter(data, x='hrv_nni_20', y='hrv_rmssd', color='feel_uncomfortable')

In [63]:
px.box(data[data['feel_at_ease'].notna()], 'imu_b_magnitude_iqr', color='feel_nervous')

In [64]:
px.box(data[data['feel_nervous'].notna()], 'gsr_SHF_var', color='feel_calm')

In [65]:
px.box(data[data['feel_nervous'].notna()], 'hrv_nni_20', color='feel_nervous')

In [66]:
reduced = {}

perplexities = [5, 10, 20]
with pd.option_context('mode.use_inf_as_na', True):
    data_i = data.copy()
    X_pre_tsne = data_i.drop(list(s_df.columns) + ['timestamp'], axis=1).dropna(how='any', axis=1)
    
    for perplexity_v in perplexities:

        X_reduced = TSNE(n_components=3, verbose=2, perplexity=perplexity_v).fit_transform(X_pre_tsne)
        dfi = pd.DataFrame({'x':X_reduced[:,0], 'y':X_reduced[:,1] , 'z':X_reduced[:,2]})
        reduced[f"perplexity_{perplexity_v}"] = dfi

[t-SNE] Computing 16 nearest neighbors...
[t-SNE] Indexed 2088 samples in 0.024s...
[t-SNE] Computed neighbors for 2088 samples in 0.303s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2088
[t-SNE] Computed conditional probabilities for sample 2000 / 2088
[t-SNE] Computed conditional probabilities for sample 2088 / 2088
[t-SNE] Mean sigma: 208.956578
[t-SNE] Computed conditional probabilities in 0.028s
[t-SNE] Iteration 50: error = 95.1422729, gradient norm = 0.1321205 (50 iterations in 1.346s)
[t-SNE] Iteration 100: error = 76.4650116, gradient norm = 0.0479102 (50 iterations in 0.609s)
[t-SNE] Iteration 150: error = 72.3359299, gradient norm = 0.0274292 (50 iterations in 0.441s)
[t-SNE] Iteration 200: error = 70.4441910, gradient norm = 0.0229025 (50 iterations in 0.415s)
[t-SNE] Iteration 250: error = 69.3631592, gradient norm = 0.0171181 (50 iterations in 0.383s)
[t-SNE] KL divergence after 250 iterations with early exaggeration: 69.363159
[t-SNE] Iteration 300: er

In [67]:
for perplexity_v in perplexities:
    dfi = reduced[f"perplexity_{perplexity_v}"]
    dfii = pd.concat([dfi,data[['tech_diff', 'feel_nervous', 'trial', 'user', 'feel_uncomfortable', 'excerpt_category','tempo']]], axis=1)
    print(dfii.head())
    fig = px.scatter_3d(dfii[dfii.trial.str.contains('trial')], x='x', y='y', z='z', color='feel_nervous')
    fig.show()
    # reduced[f"perplexity_{perplexity_v}"] = dfii

          x          y         z  tech_diff  feel_nervous  trial  user  \
0 -9.864167  25.236105 -3.796727        NaN           NaN  base1     1   
1 -9.081755  26.131111  1.907741        NaN           NaN  base1     1   
2 -9.123069  26.285538  2.424592        NaN           NaN  base1     1   
3 -5.950548  22.732794  6.130990        NaN           NaN  base1     1   
4 -5.431060  22.665051  6.534147        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


          x          y         z  tech_diff  feel_nervous  trial  user  \
0  5.244077  21.031923 -9.616042        NaN           NaN  base1     1   
1  3.244600  23.926174 -6.880806        NaN           NaN  base1     1   
2  3.019791  24.252386 -6.782335        NaN           NaN  base1     1   
3  1.172671  24.348997 -3.077808        NaN           NaN  base1     1   
4  1.687033  24.287148 -2.590580        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


           x         y         z  tech_diff  feel_nervous  trial  user  \
0  18.170851  0.301990 -4.736565        NaN           NaN  base1     1   
1  17.420588 -1.656935 -7.387177        NaN           NaN  base1     1   
2  17.239864 -1.912040 -7.407133        NaN           NaN  base1     1   
3  14.723726 -1.640428 -7.946542        NaN           NaN  base1     1   
4  14.815061 -1.544585 -8.598773        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


In [68]:
reduced_2d = {}

perplexities = [5, 10, 20]
with pd.option_context('mode.use_inf_as_na', True):
    data_i = data.copy()
    X_pre_tsne = data_i.drop(list(s_df.columns) + ['timestamp'], axis=1).dropna(how='any', axis=1)
    
    for perplexity_v in perplexities:

        X_reduced = TSNE(n_components=2, verbose=2, perplexity=perplexity_v).fit_transform(X_pre_tsne)
        dfi = pd.DataFrame({'x':X_reduced[:,0], 'y':X_reduced[:,1]})
        reduced_2d[f"perplexity_{perplexity_v}"] = dfi

[t-SNE] Computing 16 nearest neighbors...
[t-SNE] Indexed 2088 samples in 0.018s...
[t-SNE] Computed neighbors for 2088 samples in 0.301s...
[t-SNE] Computed conditional probabilities for sample 1000 / 2088
[t-SNE] Computed conditional probabilities for sample 2000 / 2088
[t-SNE] Computed conditional probabilities for sample 2088 / 2088
[t-SNE] Mean sigma: 208.956578
[t-SNE] Computed conditional probabilities in 0.023s
[t-SNE] Iteration 50: error = 96.1779404, gradient norm = 0.1757809 (50 iterations in 0.488s)
[t-SNE] Iteration 100: error = 80.5580444, gradient norm = 0.0782808 (50 iterations in 0.305s)
[t-SNE] Iteration 150: error = 76.3209076, gradient norm = 0.0611815 (50 iterations in 0.269s)
[t-SNE] Iteration 200: error = 74.0410767, gradient norm = 0.0479470 (50 iterations in 0.256s)
[t-SNE] Iteration 250: error = 72.4493942, gradient norm = 0.0478514 (50 iterations in 0.225s)
[t-SNE] KL divergence after 250 iterations with early exaggeration: 72.449394
[t-SNE] Iteration 300: er

In [69]:
for perplexity_v in perplexities:
    dfi = reduced_2d[f"perplexity_{perplexity_v}"]
    dfii = pd.concat([dfi,data[['tech_diff', 'feel_nervous', 'trial', 'user', 'feel_uncomfortable', 'excerpt_category','tempo']]], axis=1)
    print(dfii.head())
    fig = px.scatter(dfii[dfii.trial.str.contains('trial')], x='x', y='y', symbol='excerpt_category', color='tempo')
    fig.show()
    # reduced[f"perplexity_{perplexity_v}"] = dfii

           x          y  tech_diff  feel_nervous  trial  user  \
0  34.279949  58.021488        NaN           NaN  base1     1   
1  43.742462  56.578331        NaN           NaN  base1     1   
2  44.310356  56.398140        NaN           NaN  base1     1   
3  59.310493  58.433479        NaN           NaN  base1     1   
4  59.930370  58.626564        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


           x          y  tech_diff  feel_nervous  trial  user  \
0 -74.152596  29.723024        NaN           NaN  base1     1   
1 -74.587639  37.424534        NaN           NaN  base1     1   
2 -74.663879  37.928944        NaN           NaN  base1     1   
3 -69.358223  45.342602        NaN           NaN  base1     1   
4 -68.982315  46.201397        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


           x          y  tech_diff  feel_nervous  trial  user  \
0  -3.804960  63.951263        NaN           NaN  base1     1   
1  -9.909522  61.700394        NaN           NaN  base1     1   
2 -10.312634  61.541008        NaN           NaN  base1     1   
3 -11.683648  57.286106        NaN           NaN  base1     1   
4 -11.774867  56.583218        NaN           NaN  base1     1   

   feel_uncomfortable excerpt_category tempo  
0                 NaN              NaN   NaN  
1                 NaN              NaN   NaN  
2                 NaN              NaN   NaN  
3                 NaN              NaN   NaN  
4                 NaN              NaN   NaN  


In [70]:
data['u2_flag'] = data.user == 2
data['bl_flag'] = data.trial.str.contains('base')

In [71]:
px.scatter(s_df, x='user', y='trial', color='tech_diff', color_discrete_map='Alphabet')

In [72]:
px.scatter(s_df, x='user', y='excerpt', color='tech_diff', color_discrete_map='Alphabet')

In [73]:
s_df.groupby(['piece_id','tempo'])['tech_diff'].mean().sort_values()

piece_id  tempo  
3.0       slow       2.142857
4.0       slow       2.142857
5.0       slow       2.285714
2.0       slow       2.285714
4.0       fast       2.285714
5.0       fast       2.428571
3.0       fast       2.571429
7.0       slow       3.000000
18.0      slow       3.142857
8.0       slow       3.142857
9.0       slow       3.142857
2.0       fast       3.285714
1.0       slow       3.285714
10.0      fast       3.571429
          slow       3.714286
16.0      slow       4.142857
11.0      slow       4.142857
8.0       fast       4.142857
7.0       fast       4.285714
6.0       slow       4.428571
9.0       fast       4.857143
12.0      slow       5.142857
11.0      fast       5.428571
6.0       fast       5.571429
1.0       fast       5.857143
12.0      fast       6.000000
17.0      fast       7.285714
14.0      average    8.428571
15.0      average    9.571429
Name: tech_diff, dtype: float64

In [74]:
['user','excerpt','tech_diff', 'feel_calm', 'feel_at_ease', 'feel_uncomfortable', 'feel_nervous', 'emo_expr', 'tech_diff_h']

['user',
 'excerpt',
 'tech_diff',
 'feel_calm',
 'feel_at_ease',
 'feel_uncomfortable',
 'feel_nervous',
 'emo_expr',
 'tech_diff_h']

In [75]:
px.scatter(data, x='imu_a_magnitude_mean', y='tech_diff', facet_row='user')

In [76]:
px.scatter(data, x='imu_a_magnitude_mean', y='tech_diff', facet_row='user')

In [77]:
px.scatter(data, x='imu_b_magnitude_mean', y='tech_diff', facet_row='user')

In [78]:
gsr_cols = [ci for ci in data.columns if 'gsr' in ci]
